In [1]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [2]:
%pip install spuco
%pip install -q pytorch-metric-learning

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 101.0/101.0 kB 692.2 kB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 126.2/126.2 kB 4.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 78.8/78.8 kB 2.9 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
  Created wheel for littleutils: filename=littleutils-0.2.2-py3-none-any.whl size=7026 sha256=d90eb414664a5a444813761d3287395f340833611d1e9294ed7022191feab710
  Stored in directory: /root/.cache/pip/wheels/3d/fe/b0/27a9892da57472e538c7452a721a9cf463cc03cf7379889266
Successfully built littleutils
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 115.3/115.3 kB 1.8 MB/s eta 0:00:00


In [3]:
import numpy as np
import torch
import torch.nn as nn
import torch.nn.functional as F
import torchvision.transforms as T
from torch.utils.data import DataLoader, Dataset
from spuco.datasets import SpuCoMNIST, SpuriousFeatureDifficulty
import torchvision.transforms as transforms
import cv2
import torchvision.models as models
from pytorch_metric_learning import losses
import torch.optim as optim
from torch.optim import lr_scheduler
import os

#device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
#Use CPU for analysis
device = "cpu"

In [8]:
magnitude = "MEDIUM"

magnitude_dict = {
    "SMALL": SpuriousFeatureDifficulty.MAGNITUDE_SMALL,
    "MEDIUM":SpuriousFeatureDifficulty.MAGNITUDE_MEDIUM,
    "LARGE":SpuriousFeatureDifficulty.MAGNITUDE_LARGE,
}

class Config:
  spurious_correlation_strength  = 0.995
  spurious_feature_difficulty = magnitude_dict[magnitude]
  label_noise = 0.001
  size = 28
  flip_probability = 0.5
  batch_size = 256
  backbone_pretrained = False
  projection_dim = 128
  T_max = 10
  lr = 5e-4
  min_lr = 1e-5
  weight_decay = 1e-6
  temperature = 0.5

In [9]:
model_type = 'simCLR'
save_dir = f"/content/drive/MyDrive/CS260D_final_project/plots/simCLR/{Config.spurious_correlation_strength}_{magnitude}"
if not os.path.isdir(save_dir):
  os.makedirs(save_dir)

# Setup Data


In [10]:
classes = [[0, 1], [2, 3], [4, 5], [6, 7], [8, 9]]

trainset = SpuCoMNIST(
    root="/data/mnist/",
    spurious_feature_difficulty=Config.spurious_feature_difficulty,
    spurious_correlation_strength=Config.spurious_correlation_strength,
    classes=classes,
    split="train",
    label_noise=Config.label_noise
)
trainset.initialize()

valset = SpuCoMNIST(
    root="/data/mnist/",
    spurious_feature_difficulty=Config.spurious_feature_difficulty,
    spurious_correlation_strength=Config.spurious_correlation_strength,
    classes=classes,
    split="test",
    label_noise=Config.label_noise
)
valset.initialize()


100%|██████████| 10000/10000 [00:02<00:00, 4387.94it/s]


In [11]:
len(trainset)

48004

In [12]:
len(valset)

10000

In [13]:
# Show example from each group
from IPython.display import display
for (k, v) in trainset.group_partition.items():
  print(f"Group: {k}, Qty: {len(v)}")
  img = T.ToPILImage()(trainset[v[0]][0])
  display(img)

Group: (2, 2), Qty: 8953


Group: (0, 0), Qty: 10076


Group: (4, 4), Qty: 9380


Group: (1, 1), Qty: 9615


Group: (3, 3), Qty: 9689


...

Group: (4, 3), Qty: 11


Group: (2, 0), Qty: 5


Group: (2, 3), Qty: 16


Group: (0, 2), Qty: 14


Group: (3, 4), Qty: 10


In [ ]:

## Augmentation
from torchvision.transforms import v2

size = 28
train_transform = transforms.Compose([
    v2.ToImage(),
    v2.RandomResizedCrop(size),
    v2.RandomHorizontalFlip(p=0.5),
    v2.RandomApply([transforms.ColorJitter(0.4, 0.4, 0.4, 0.1)], p=0.8),
    v2.RandomGrayscale(p=0.2),
    v2.ToTensor(),
    v2.Normalize([0.4914, 0.4822, 0.4465], [0.2023, 0.1994, 0.2010])])

test_transform = transforms.Compose([
    v2.ToImage(),
    v2.ToTensor(),
    v2.Normalize([0.4914, 0.4822, 0.4465], [0.2023, 0.1994, 0.2010])])

/usr/local/lib/python3.10/dist-packages/torchvision/transforms/v2/_deprecated.py:43: UserWarning: The transform `ToTensor()` is deprecated and will be removed in a future release. Instead, please use `v2.Compose([v2.ToImage(), v2.ToDtype(torch.float32, scale=True)])`.
  warnings.warn(


In [ ]:
class SpucoDataset(Dataset):
    def __init__(self, dataset, transform=None):
        self.dataset = dataset
        self.transform = transform

    def __len__(self):
        return len(self.dataset)

    def __getitem__(self, index):
        img = self.dataset[index][0]
        label = self.dataset[index][1]

        if self.transform is None:
          return img, label

        augmented_img = self.transform(img)
        return (img, augmented_img), label

In [ ]:
train_dataset = SpucoDataset(trainset, train_transform)
val_dataset = SpucoDataset(valset, test_transform)

dataloaders = {'train': DataLoader(dataset=train_dataset, batch_size=Config.batch_size, num_workers=2, pin_memory=True, shuffle=True),
         'eval': DataLoader(dataset=val_dataset, batch_size=Config.batch_size, num_workers=2, pin_memory=True, shuffle=False)}

# Setup Model

In [ ]:
## https://kevinmusgrave.github.io/pytorch-metric-learning/losses/#ntxentloss
## https://kevinmusgrave.github.io/pytorch-metric-learning/losses/#selfsupervisedloss
criterion = losses.NTXentLoss(temperature=Config.temperature)
criterion = losses.SelfSupervisedLoss(criterion)

In [ ]:
## https://github.com/berfukaraca/SSL-Cifar10-ContrastiveLearning/blob/main/colab_notebooks/SSL_SimCLR_Cifar10_CL.ipynb

class SimCLR_model(nn.Module):
    def __init__(self, base_encoder, projection_dim, n_features):
        super(SimCLR_model, self).__init__()
        self.n_features = n_features
        self.base_encoder = base_encoder

        self.projectionHead = nn.Sequential(
            nn.Linear(self.n_features, self.n_features, bias=False),
            nn.BatchNorm1d(self.n_features),
            nn.ReLU(), #non-linearity
            nn.Linear(self.n_features, projection_dim, bias=False),
            nn.BatchNorm1d(projection_dim),
        )

    def forward(self, x_i):
        out = self.projectionHead(self.base_encoder(x_i))

        return out

In [ ]:
## model and optimizer
model = models.resnet50()
# print(model)
clr_model = SimCLR_model(model, Config.projection_dim, 1000) ## output dimension of resnet18 is 1000
optimizer = optim.Adam(clr_model.parameters(), lr=Config.lr, weight_decay=Config.weight_decay)
## cosine annealing lr: https://arxiv.org/pdf/1608.03983.pdf
scheduler = lr_scheduler.CosineAnnealingLR(optimizer, T_max=Config.T_max, eta_min=Config.min_lr)

clr_model.to(device)

SimCLR_model(
  (base_encoder): ResNet(
    (conv1): Conv2d(3, 64, kernel_size=(7, 7), stride=(2, 2), padding=(3, 3), bias=False)
    (bn1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (relu): ReLU(inplace=True)
    (maxpool): MaxPool2d(kernel_size=3, stride=2, padding=1, dilation=1, ceil_mode=False)
    (layer1): Sequential(
      (0): Bottleneck(
        (conv1): Conv2d(64, 64, kernel_size=(1, 1), stride=(1, 1), bias=False)
        (bn1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
        (conv2): Conv2d(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
        (bn2): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
        (conv3): Conv2d(64, 256, kernel_size=(1, 1), stride=(1, 1), bias=False)
        (bn3): BatchNorm2d(256, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
        (relu): ReLU(inplace=True)
        (downsample): Sequential(


In [ ]:
## Load the pre-trained model parameters

checkpoints_path = f"/content/drive/MyDrive/CS260D_final_project/changing_spurious_correlation_strength/model_parameters/{Config.spurious_correlation_strength}_{magnitude}/"
# checkpoints_path = f"/content/drive/MyDrive/CS260D_final_project/model_parameters/"
# find model
model_path = os.path.join(checkpoints_path, f'paramsend_bs_restart_r.pt')

checkpoint = torch.load(model_path, map_location = torch.device(device))
loss= checkpoint['loss']
epoch = checkpoint['epoch']

clr_model.load_state_dict(checkpoint['net'])

<All keys matched successfully>

In [ ]:
# Check Loss
loss/len(dataloaders['train'])


0.025153009356714145

In [ ]:
epoch

20

In [ ]:
## Generate tensor of all embeddings and targets on CPU

import matplotlib.pyplot as plt
import pandas as pd
from sklearn.decomposition import PCA

torch.cuda.empty_cache()
device = 'cpu'
clr_model.to(device)

embeddings = []
targets = []

for batch_idx, ((images, _), labels) in enumerate(dataloaders['eval']):
  embeddings.append(clr_model(images).detach().cpu())
  targets.append(labels)
  torch.cuda.empty_cache()


# clr_model = None

embeddings = torch.cat(embeddings).detach().cpu().numpy()
targets = torch.cat(targets).cpu().numpy()

# Data Analysis

In [ ]:
comp = 32
pca = PCA(n_components=comp)
pca_emb = pca.fit_transform(embeddings)
PCs = pd.DataFrame(pca_emb)
PCs.columns = [f"PC{i+ 1}" for i in range(comp)]
embs = pd.concat([pd.DataFrame(embeddings),PCs], axis=1, join='inner')

In [ ]:
# Check singular values for pca
pca.singular_values_

array([343.79788 , 339.70358 , 332.45706 , 315.7641  , 300.0318  ,
       292.00278 , 277.15253 , 269.79922 , 256.68402 , 237.08818 ,
       229.44127 , 217.01761 , 211.85599 , 205.19064 , 200.24118 ,
       185.03288 , 174.27357 , 167.06688 , 146.53375 , 135.19832 ,
       101.30411 ,  66.85176 ,  36.536366,  25.27174 ,  17.23018 ,
        14.259046,  12.616002,  11.488041,  10.238638,   9.648964,
         9.188709,   8.512127], dtype=float32)

In [ ]:
# Add labels to embedding df
embs['true_label'] = targets
for (true, spur), idxs in valset.group_partition.items():
  for i in idxs:
    embs.loc[i, 'spurious_label'] = spur
embs['spurious_label'] = embs['spurious_label'].astype(int)

## Full Data Analysis

### PCA

In [ ]:
import plotly as py
import plotly.graph_objs as go
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot

traces = []
for (true_label, spurious_label), df in embs.groupby(['true_label', 'spurious_label']):
  traces.append(go.Scatter(x = df['PC1'],
                           y = df['PC2'],
                           mode = "markers",
                           name = f"True label {true_label}, Spurious label {spurious_label}",
                           text = None,
                           marker = dict(size = 4)
                           )
  )
title = "PCA analysis of Validation Data by Group"
layout = dict(title = title,
              xaxis= dict(title= 'PC1',ticklen= 5,zeroline= False),
              yaxis= dict(title= 'PC2',ticklen= 5,zeroline= False),
              height = 1000,
              width = 1000
             )

fig = dict(data = traces, layout = layout)
iplot(fig)
save_name = f"{model_type}_{Config.spurious_correlation_strength}_{magnitude}_PCA_alldata_by_groups.html"
go.Figure.write_html(fig, os.path.join(save_dir, save_name))

In [ ]:
import plotly as py
import plotly.graph_objs as go
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot

traces = []
for true_label, df in embs.groupby(['true_label']):
  traces.append(go.Scatter(x = df['PC1'],
                           y = df['PC2'],
                           mode = "markers",
                           name = f"True label {true_label}",
                           text = None,
                           marker = dict(size = 4)
                           )
  )
title = "PCA analysis of Validation Data by True Label"
layout = dict(title = title,
              xaxis= dict(title= 'PC1',ticklen= 5,zeroline= False),
              yaxis= dict(title= 'PC2',ticklen= 5,zeroline= False),
              height = 1000,
              width = 1000
             )

fig = dict(data = traces, layout = layout)
iplot(fig)
save_name = f"{model_type}_{Config.spurious_correlation_strength}_{magnitude}_PCA_alldata_by_truelabel.html"
go.Figure.write_html(fig, os.path.join(save_dir, save_name))

<ipython-input-22-4a5026f7690c>:6: FutureWarning:

In a future version of pandas, a length 1 tuple will be returned when iterating over a groupby with a grouper equal to a list of length 1. Don't supply a list with a single grouper to avoid this warning.



In [ ]:
import plotly as py
import plotly.graph_objs as go
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot

traces = []
for spurious_label, df in embs.groupby(['spurious_label']):
  traces.append(go.Scatter(x = df['PC1'],
                           y = df['PC2'],
                           mode = "markers",
                           name = f"Spurious label {spurious_label}",
                           text = None,
                           marker = dict(size = 4)
                           )
  )
title = "PCA analysis of Validation Data by Spurious Label"
layout = dict(title = title,
              xaxis= dict(title= 'PC1',ticklen= 5,zeroline= False),
              yaxis= dict(title= 'PC2',ticklen= 5,zeroline= False),
              height = 1000,
              width = 1000
             )

fig = dict(data = traces, layout = layout)
iplot(fig)
save_name = f"{model_type}_{Config.spurious_correlation_strength}_{magnitude}_PCA_alldata_by_spuriouslabel.html"
go.Figure.write_html(fig, os.path.join(save_dir, save_name))

<ipython-input-23-409e73fd8e41>:6: FutureWarning:

In a future version of pandas, a length 1 tuple will be returned when iterating over a groupby with a grouper equal to a list of length 1. Don't supply a list with a single grouper to avoid this warning.



### t-SNE

In [ ]:
from sklearn.manifold import TSNE

for perplexity in [15, 30, 50]:

#T-SNE with two dimensions
  tsne = TSNE(n_components=2, perplexity=perplexity, n_iter = 3000)

  TCs = pd.DataFrame(tsne.fit_transform(embeddings))
  TCs.columns = ["TC1","TC2"]
  TCs['true_label'] = embs['true_label']
  TCs['spurious_label'] = embs['spurious_label']
  # Find best perplexity value
  traces = []
  for (true_label, spurious_label), df in TCs.groupby(['true_label', 'spurious_label']):
    traces.append(go.Scatter(x = df['TC1'], y = df['TC2'], mode = "markers", name = f"True label {true_label}, Spurious label {spurious_label}", text = None))

  title = f"t-SNE Cluster Visualization of Embedded Data, Perplexity = {perplexity}"
  layout = dict(title = title,
                xaxis= dict(title= 'TC1',ticklen= 5,zeroline= False),
                yaxis= dict(title= 'TC2',ticklen= 5,zeroline= False),
                width = 1000,
                height = 1000
                #zaxis= dict(title= 'TC3',ticklen= 5,zeroline= False)
              )

  fig = dict(
      data = traces,
      layout = layout
  )
  iplot(fig)

  save_name = f"{model_type}_{Config.spurious_correlation_strength}_{magnitude}_TSNE_perplexity{perplexity}_alldata_by_groups.html"
  go.Figure.write_html(fig, os.path.join(save_dir, save_name))


# tsne_embs = pd.concat([embs,TCs], axis=1, join='inner')

In [ ]:
from sklearn.manifold import TSNE

for perplexity in [15, 30, 50]:

#T-SNE with two dimensions
  tsne = TSNE(n_components=2, perplexity=perplexity, n_iter = 3000)

  TCs = pd.DataFrame(tsne.fit_transform(embeddings))
  TCs.columns = ["TC1","TC2"]
  TCs['true_label'] = embs['true_label']
  TCs['spurious_label'] = embs['spurious_label']
  # Find best perplexity value
  traces = []
  for true_label, df in TCs.groupby(['true_label']):
    traces.append(go.Scatter(x = df['TC1'], y = df['TC2'], mode = "markers", name = f"True label {true_label}", text = None))

  title = f"t-SNE Cluster Visualization of Embedded Data Grouped by True Label, Perplexity = {perplexity}"
  layout = dict(title = title,
                xaxis= dict(title= 'TC1',ticklen= 5,zeroline= False),
                yaxis= dict(title= 'TC2',ticklen= 5,zeroline= False),
                width = 1000,
                height = 1000
                #zaxis= dict(title= 'TC3',ticklen= 5,zeroline= False)
              )

  fig = dict(
      data = traces,
      layout = layout
  )
  iplot(fig)

  save_name = f"{model_type}_{Config.spurious_correlation_strength}_{magnitude}_TSNE_perplexity{perplexity}_alldata_by_truelabel.html"
  go.Figure.write_html(fig, os.path.join(save_dir, save_name))


# tsne_embs = pd.concat([embs,TCs], axis=1, join='inner')

<ipython-input-25-173cbd2d105d>:14: FutureWarning:

In a future version of pandas, a length 1 tuple will be returned when iterating over a groupby with a grouper equal to a list of length 1. Don't supply a list with a single grouper to avoid this warning.



<ipython-input-25-173cbd2d105d>:14: FutureWarning:

In a future version of pandas, a length 1 tuple will be returned when iterating over a groupby with a grouper equal to a list of length 1. Don't supply a list with a single grouper to avoid this warning.



<ipython-input-25-173cbd2d105d>:14: FutureWarning:

In a future version of pandas, a length 1 tuple will be returned when iterating over a groupby with a grouper equal to a list of length 1. Don't supply a list with a single grouper to avoid this warning.



In [ ]:
from sklearn.manifold import TSNE

for perplexity in [15, 30, 50]:

#T-SNE with two dimensions
  tsne = TSNE(n_components=2, perplexity=perplexity, n_iter = 3000)

  TCs = pd.DataFrame(tsne.fit_transform(embeddings))
  TCs.columns = ["TC1","TC2"]
  TCs['true_label'] = embs['true_label']
  TCs['spurious_label'] = embs['spurious_label']
  # Find best perplexity value
  traces = []
  for spurious_label, df in TCs.groupby(['spurious_label']):
    traces.append(go.Scatter(x = df['TC1'], y = df['TC2'], mode = "markers", name = f"Spurious label {spurious_label}", text = None))

  title = f"t-SNE Cluster Visualization of Embedded Data Grouped by Spurious Label, Perplexity = {perplexity}"
  layout = dict(title = title,
                xaxis= dict(title= 'TC1',ticklen= 5,zeroline= False),
                yaxis= dict(title= 'TC2',ticklen= 5,zeroline= False),
                width = 1000,
                height = 1000
                #zaxis= dict(title= 'TC3',ticklen= 5,zeroline= False)
              )

  fig = dict(
      data = traces,
      layout = layout
  )
  iplot(fig)

  save_name = f"{model_type}_{Config.spurious_correlation_strength}_{magnitude}_TSNE_perplexity{perplexity}_alldata_by_spuriouslabel.html"
  go.Figure.write_html(fig, os.path.join(save_dir, save_name))


# tsne_embs = pd.concat([embs,TCs], axis=1, join='inner')

<ipython-input-26-3e5136d599d5>:14: FutureWarning:

In a future version of pandas, a length 1 tuple will be returned when iterating over a groupby with a grouper equal to a list of length 1. Don't supply a list with a single grouper to avoid this warning.



<ipython-input-26-3e5136d599d5>:14: FutureWarning:

In a future version of pandas, a length 1 tuple will be returned when iterating over a groupby with a grouper equal to a list of length 1. Don't supply a list with a single grouper to avoid this warning.



<ipython-input-26-3e5136d599d5>:14: FutureWarning:

In a future version of pandas, a length 1 tuple will be returned when iterating over a groupby with a grouper equal to a list of length 1. Don't supply a list with a single grouper to avoid this warning.



### PCA --> t-SNE

In [ ]:
from sklearn.manifold import TSNE

for perplexity in [30, 50, 100]:

#T-SNE with two dimensions
  tsne = TSNE(n_components=2, perplexity=perplexity, n_iter = 3000)

  TCs = pd.DataFrame(tsne.fit_transform(pca_emb))
  TCs.columns = ["TC1","TC2"]
  TCs['true_label'] = embs['true_label']
  TCs['spurious_label'] = embs['spurious_label']
  # Find best perplexity value
  traces = []
  for (true_label, spurious_label), df in TCs.groupby(['true_label', 'spurious_label']):
    traces.append(go.Scatter(x = df['TC1'], y = df['TC2'], mode = "markers", name = f"True label {true_label}, Spurious label {spurious_label}", text = None))

  title = f"t-SNE Cluster Visualization of PCA Embedded Data, Perplexity = {perplexity}"
  layout = dict(title = title,
                xaxis= dict(title= 'TC1',ticklen= 5,zeroline= False),
                yaxis= dict(title= 'TC2',ticklen= 5,zeroline= False),
                width = 1000,
                height = 1000
                #zaxis= dict(title= 'TC3',ticklen= 5,zeroline= False)
              )

  fig = dict(
      data = traces
  )
  iplot(fig)


  save_name = f"{model_type}_{Config.spurious_correlation_strength}_{magnitude}_PCAtoTSNE_perplexity{perplexity}_alldata_by_groups.html"
  go.Figure.write_html(fig, os.path.join(save_dir, save_name))

# tsne_embs = pd.concat([embs,TCs], axis=1, join='inner')

## Analysis in Each True Label

### PCA

In [ ]:
true_label_clusters_pca = {
    # True label: embedding dataframe
}
for l, true_cluster in embs.groupby('true_label'):
  true_emb = true_cluster.iloc[:, :128].values
  comp = 15
  pca = PCA(n_components=comp)

  PCs = pd.DataFrame(pca.fit_transform(true_emb), columns = [f"PC{i+ 1}_TL" for i in range(comp)])
  PCs = pd.concat([PCs,true_cluster[['true_label', 'spurious_label']]], axis=1, join='inner')
  true_label_clusters_pca[l] = PCs
  print(pca.singular_values_)
  # pca_embs = pd.concat([pd.DataFrame(embeddings),PCs_2d], axis=1, join='inner')


[286.96887  252.5397   169.354    139.3023    81.53729   77.53682
  61.806583  49.787086  42.603924  29.73973   27.46843   24.921389
  22.093817  16.662483  16.17803 ]
[254.01576  211.51297  173.29765  126.08218  112.471756 101.19392
  86.638664  75.976036  65.725006  49.955204  41.677956  40.164143
  30.918571  27.78242   23.974699]
[259.47034  176.28288  152.15286  135.67453  122.10395   93.432495
  83.97974   70.22167   57.386482  53.042725  45.086163  39.919285
  37.4073    32.443653  31.06746 ]
[281.6699   181.02565  177.47972  138.138    116.235756 106.06696
 101.869     71.606766  69.14561   65.65281   50.324215  46.039562
  44.711784  38.788677  33.220448]
[230.75218  203.1881   153.63594  136.79178  110.906494  80.44704
  72.62512   62.546158  51.33451   43.930374  38.77362   35.98477
  31.542744  27.366667  24.985512]


In [ ]:
import os

for k, v in true_label_clusters_pca.items():
  traces = []
  for s in np.sort(v['spurious_label'].unique()):
    group = v[v['spurious_label'] == s]
    traces.append(go.Scatter(
                      x = group['PC1_TL'],
                      y = group['PC2_TL'],
                      #z = group['PC3_TL'],
                      mode = "markers",
                      name = f"Subgroup {s}",
                      text = None))
  data = traces

  title = f"True Label {k} PCA"

  layout = dict(title = title,
                xaxis= dict(title= 'PC1',ticklen= 5,zeroline= False),
                yaxis= dict(title= 'PC2',ticklen= 5,zeroline= False),
                width = 1000,
                height = 1000
              )

  fig = dict(data = data, layout = layout)


  iplot(fig)
  save_name = f"{model_type}_{Config.spurious_correlation_strength}_{magnitude}_PCA_on_TL{k}.html"
  go.Figure.write_html(fig, os.path.join(save_dir, save_name))

### t-SNE

In [ ]:
true_label_clusters_tsne = {
    # True label: embedding dataframe
}
for l, true_cluster in embs.groupby('true_label'):
  true_emb = true_cluster.iloc[:, :128].values
  comp = 2
  tsne = TSNE(n_components=comp)

  TCs = pd.DataFrame(tsne.fit_transform(true_emb), columns = [f"TC{i+ 1}_TL" for i in range(comp)])
  TCs = pd.concat([TCs,true_cluster[['true_label', 'spurious_label']]], axis=1, join='inner')
  true_label_clusters_tsne[l] = TCs
  # pca_embs = pd.concat([pd.DataFrame(embeddings),PCs_2d], axis=1, join='inner')


In [ ]:
from sklearn.manifold import TSNE

for perplexity in [15, 30, 50]:
  true_label_clusters_tsne = {
    # True label: embedding dataframe
  }
  for l, true_cluster in embs.groupby('true_label'):
    true_emb = true_cluster.iloc[:, :128].values
    comp = 2
    tsne = TSNE(n_components=comp, perplexity = perplexity, n_iter = 3000)

    TCs = pd.DataFrame(tsne.fit_transform(true_emb), columns = [f"TC{i+ 1}_TL" for i in range(comp)])
    TCs = pd.concat([TCs,true_cluster[['true_label', 'spurious_label']]], axis=1, join='inner')
    true_label_clusters_tsne[l] = TCs

  for k, v in true_label_clusters_tsne.items():
    traces = []
    for s in np.sort(v['spurious_label'].unique()):
      group = v[v['spurious_label'] == s]
      traces.append(go.Scatter(
                        x = group['TC1_TL'],
                        y = group['TC2_TL'],
                        #z = group['TC3_TL'],
                        mode = "markers",
                        name = f"Spurious Label {s}",
                        text = None,
                        marker = dict(size = 4)
                        ))
    data = traces

    title = f"t-SNE Analysis of Spurious Label {k} Embeddings, Perplexity {perplexity}"

    layout = dict(title = title,
                  xaxis= dict(title= 'TC1',ticklen= 5,zeroline= False),
                  yaxis= dict(title= 'TC2',ticklen= 5,zeroline= False),
                  #zaxis= dict(title= 'TC3',ticklen= 5,zeroline= False)
                  width = 1000,
                  height = 1000
                )

    fig = dict(data = data, layout = layout)
    iplot(fig)
    save_name = f"{model_type}_{Config.spurious_correlation_strength}_{magnitude}_TSNE_perplexity{perplexity}_on_TL{k}.html"
    go.Figure.write_html(fig, os.path.join(save_dir, save_name))
  # pca_embs = pd.concat([pd.DataFrame(embeddings),PCs_2d], axis=1, join='inner')


### PCA --> t-SNE

In [ ]:
from sklearn.manifold import TSNE

for perplexity in [15, 30, 50]:
  true_label_clusters_pca_tsne = {
    # True label: embedding dataframe
  }
  for l, true_cluster_pca_df in true_label_clusters_pca.items():
    true_emb = true_cluster_pca_df.iloc[:, :-2].values
    comp = 2
    tsne = TSNE(n_components=comp, perplexity = perplexity, n_iter = 3000)

    TCs = pd.DataFrame(tsne.fit_transform(true_emb), columns = [f"TC{i+ 1}_TL" for i in range(comp)])
    TCs = pd.concat([TCs,true_cluster_pca_df[['true_label', 'spurious_label']]], axis=1, join='inner')
    true_label_clusters_pca_tsne[l] = TCs

  for k, v in true_label_clusters_pca_tsne.items():
    traces = []
    for s in np.sort(v['spurious_label'].unique()):
      group = v[v['spurious_label'] == s]
      traces.append(go.Scatter(
                        x = group['TC1_TL'],
                        y = group['TC2_TL'],
                        #z = group['TC3_TL'],
                        mode = "markers",
                        name = f"Spurious Label {s}",
                        text = None,
                        marker = dict(size = 4)
                        ))
    data = traces

    title = f"t-SNE Analysis of True Label {k} PCA Embeddings, Perplexity {perplexity}"

    layout = dict(title = title,
                  xaxis= dict(title= 'TC1',ticklen= 5,zeroline= False),
                  yaxis= dict(title= 'TC2',ticklen= 5,zeroline= False),
                  #zaxis= dict(title= 'TC3',ticklen= 5,zeroline= False)
                  width = 1000,
                  height = 1000
                )

    fig = dict(data = data, layout = layout)
    iplot(fig)
    save_name = f"{model_type}_{Config.spurious_correlation_strength}_{magnitude}_PCAtoTSNE_perplexity{perplexity}_on_TL{k}.html"
    go.Figure.write_html(fig, os.path.join(save_dir, save_name))
  # pca_embs = pd.concat([pd.DataFrame(embeddings),PCs_2d], axis=1, join='inner')


## Analysis in Each Spurious Label

### PCA

In [ ]:
spurious_label_clusters_pca = {
    # True label: embedding dataframe
}
for l, spurious_cluster in embs.groupby('spurious_label'):
  spur_emb = spurious_cluster.iloc[:, :128].values
  comp = 15
  pca = PCA(n_components=comp)

  PCs = pd.DataFrame(pca.fit_transform(spur_emb), columns = [f"PC{i+ 1}_TL" for i in range(comp)])
  PCs = pd.concat([PCs,spurious_cluster[['true_label', 'spurious_label']]], axis=1, join='inner')
  spurious_label_clusters_pca[l] = PCs
  print(pca.singular_values_)
  # pca_embs = pd.concat([pd.DataFrame(embeddings),PCs_2d], axis=1, join='inner')


[153.1728   152.60696  149.57314  140.37335  132.27116  129.79913
 122.53396  121.210915 116.966705 105.49672  103.21981   97.389145
  96.21975   91.22326   89.04464 ]
[155.30695  153.15732  150.13168  138.16116  134.93277  132.1688
 121.750885 120.22813  112.126785 107.09883  101.13511   96.41494
  92.79451   91.71859   88.415474]
[156.039    150.29964  149.24466  145.23055  135.02881  129.58965
 125.72238  117.992165 116.7308   106.162964 100.6678    98.396416
  92.73935   92.61517   88.64361 ]
[157.92433  152.13754  146.38022  143.2302   133.54308  131.17383
 123.89194  119.23603  112.53336  107.32856  103.77174   98.13901
  91.46134   90.75691   90.380974]
[155.88213  151.91737  147.6158   140.60553  133.95706  129.7522
 126.02171  123.39148  113.935555 105.000015 104.04061   99.842705
  93.74008   90.379616  86.80802 ]


In [ ]:
for k, v in spurious_label_clusters_pca.items():
  traces = []
  for s in np.sort(v['true_label'].unique()):
    group = v[v['true_label'] == s]
    traces.append(go.Scatter(
                      x = group['PC1_TL'],
                      y = group['PC2_TL'],
                      #z = group['PC3_TL'],
                      mode = "markers",
                      name = f"Subgroup {s}",
                      text = None))
  data = traces

  title = f"Spurious Label {k} PCA"

  layout = dict(title = title,
                xaxis= dict(title= 'PC1',ticklen= 5,zeroline= False),
                yaxis= dict(title= 'PC2',ticklen= 5,zeroline= False),
                width = 1000,
                height = 1000
              )

  fig = dict(data = data, layout = layout)


  iplot(fig)
  save_name = f"{model_type}_{Config.spurious_correlation_strength}_{magnitude}_PCA_on_SL{k}.html"
  go.Figure.write_html(fig, os.path.join(save_dir, save_name))

### t-SNE

In [ ]:
spurious_label_clusters_tsne = {
    # True label: embedding dataframe
}
for l, spurious_cluster in embs.groupby('spurious_label'):
  spur_emb = spurious_cluster.iloc[:, :128].values
  comp = 2
  tsne = TSNE(n_components=comp)

  TCs = pd.DataFrame(tsne.fit_transform(spur_emb), columns = [f"TC{i+ 1}_TL" for i in range(comp)])
  TCs = pd.concat([TCs,spurious_cluster[['true_label', 'spurious_label']]], axis=1, join='inner')
  spurious_label_clusters_tsne[l] = TCs
  # pca_embs = pd.concat([pd.DataFrame(embeddings),PCs_2d], axis=1, join='inner')


In [ ]:
for perplexity in [15, 30, 50]:
  spurious_label_clusters_tsne = {
    # True label: embedding dataframe
  }
  for l, spurious_cluster in embs.groupby('spurious_label'):
    spur_emb = spurious_cluster.iloc[:, :128].values
    comp = 2
    tsne = TSNE(n_components=comp, perplexity = perplexity, n_iter = 3000)

    TCs = pd.DataFrame(tsne.fit_transform(spur_emb), columns = [f"TC{i+ 1}_TL" for i in range(comp)])
    TCs = pd.concat([TCs,spurious_cluster[['true_label', 'spurious_label']]], axis=1, join='inner')
    spurious_label_clusters_tsne[l] = TCs

  for k, v in spurious_label_clusters_tsne.items():
    traces = []
    for s in np.sort(v['true_label'].unique()):
      group = v[v['true_label'] == s]
      traces.append(go.Scatter(
                        x = group['TC1_TL'],
                        y = group['TC2_TL'],
                        #z = group['TC3_TL'],
                        mode = "markers",
                        name = f"True Label {s}",
                        text = None,
                        marker = dict(size = 4)
                        ))
    data = traces

    title = f"t-SNE Analysis of Spurious Label {k} Embeddings, Perplexity {perplexity}"

    layout = dict(title = title,
                  xaxis= dict(title= 'TC1',ticklen= 5,zeroline= False),
                  yaxis= dict(title= 'TC2',ticklen= 5,zeroline= False),
                  #zaxis= dict(title= 'TC3',ticklen= 5,zeroline= False)
                  width = 1000,
                  height = 1000
                )

    fig = dict(data = data, layout = layout)
    iplot(fig)
    save_name = f"{model_type}_{Config.spurious_correlation_strength}_{magnitude}_TSNE_perplexity{perplexity}_on_SL{k}.html"
    go.Figure.write_html(fig, os.path.join(save_dir, save_name))
  # pca_embs = pd.concat([pd.DataFrame(embeddings),PCs_2d], axis=1, join='inner')


### PCA --> t-SNE

In [ ]:
for perplexity in [15, 30, 50]:
  spurious_label_clusters_pca_tsne = {
    # True label: embedding dataframe
  }
  for l, spurious_cluster_pca_df in spurious_label_clusters_pca.items():
    spurious_emb = spurious_cluster_pca_df.iloc[:, :-2].values
    comp = 2
    tsne = TSNE(n_components=comp, perplexity = perplexity, n_iter = 3000)

    TCs = pd.DataFrame(tsne.fit_transform(spurious_emb), columns = [f"TC{i+ 1}_TL" for i in range(comp)])
    TCs = pd.concat([TCs,spurious_cluster_pca_df[['true_label', 'spurious_label']]], axis=1, join='inner')
    spurious_label_clusters_pca_tsne[l] = TCs

  for k, v in spurious_label_clusters_pca_tsne.items():
    traces = []
    for s in np.sort(v['true_label'].unique()):
      group = v[v['true_label'] == s]
      traces.append(go.Scatter(
                        x = group['TC1_TL'],
                        y = group['TC2_TL'],
                        #z = group['TC3_TL'],
                        mode = "markers",
                        name = f"True Label {s}",
                        text = None,
                        marker = dict(size = 4)
                        ))
    data = traces

    title = f"T-SNE Analysis of Spurious Label {k} PCA Embeddings, Perplexity {perplexity}"

    layout = dict(title = title,
                  xaxis= dict(title= 'TC1',ticklen= 5,zeroline= False),
                  yaxis= dict(title= 'TC2',ticklen= 5,zeroline= False),
                  #zaxis= dict(title= 'TC3',ticklen= 5,zeroline= False)
                  width = 1000,
                  height = 1000
                )

    fig = dict(data = data, layout = layout)
    iplot(fig)
    save_name = f"{model_type}_{Config.spurious_correlation_strength}_{magnitude}_PCAtoTSNE_perplexity{perplexity}_on_SL{k}.html"
    go.Figure.write_html(fig, os.path.join(save_dir, save_name))
  # pca_embs = pd.concat([pd.DataFrame(embeddings),PCs_2d], axis=1, join='inner')
